In [1]:
import h5py
import pandas as pd
from pathlib import Path
import SomnoMed as som
import numpy as np

import sys
import os

sys.path.append('../som-gcnn/data/')

from pg import PGManager
from undercut_depth_v3 import find_undercut_depth
import datetime

# h5py.run_tests()

In [24]:
# %%time
with PGManager(database='som_retention', password='rd_root_passwd') as pg:
    arch_metadata_df = pd.read_sql('select * from arch_metadata', pg.connection)
    arch_files_df = pd.read_sql('select case_id, side, arch_cad_stage_2, relative_directory from arch_files', pg.connection)
    feature_files_df = pd.read_sql('select case_id, side, arch_cad_fit from feature_files', pg.connection)
    arch_retention_values_df = pd.read_sql('select * from arch_retention_values', pg.connection)
    # arch_retention_values_df = arch_files_df[['case_id', 'side']]
    # arch_retention_values_df[['first_cam_retention_left', 'first_cam_retention_anterior', 'first_cam_retention_right']] = pd.DataFrame(np.zeros((len(arch_files_df),3)))
    arch_retention_coordinates_df = pd.read_sql('select * from arch_retention_coordinates where hole_search_failed = false and coords_verified = true', pg.connection)

raw_df = arch_metadata_df.merge(arch_files_df, on=['case_id', 'side']).merge(feature_files_df, on=['case_id', 'side']).merge(arch_retention_values_df, on=['case_id', 'side']).merge(arch_retention_coordinates_df, on=['case_id', 'side'])
raw_df


/home/josh/.local/lib/python3.8/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
/home/josh/.local/lib/python3.8/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
/home/josh/.local/lib/python3.8/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(
/home/josh/.local/lib/python3.8/site-packages/pandas/io/sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string

case_id   side first_cam_retention_date         product country  \
0           SE57420  lower               2021-12-02           avant      SE   
1         NLD183727  upper               2022-04-11           avant     NLD   
2         NLD183727  lower               2022-04-11           avant     NLD   
3           DK59888  upper               2022-03-16           avant      SE   
4      POUSA0097278  upper               2021-12-01           avant     USA   
...             ...    ...                      ...             ...     ...   
29346  POUSA0085214  lower               2021-08-21  herbst_advance     USA   
29347  POUSA0087329  upper               2021-08-21  herbst_advance     USA   
29348  POUSA0087329  lower               2021-08-21  herbst_advance     USA   
29349  POUSA0087258  upper               2021-08-21  herbst_advance     USA   
29350  POUSA0087258  lower               2021-08-21  herbst_advance     USA   

             batch       arch_cad_stage_2  \
0      46020211126       SE57420 {L2}.stl   
1      31020220401     NLD183727 {U2}.stl   
2      31020220401     NLD183727 {L2}.stl   
3      46020220309       DK59888 {U2}.stl   
4         10017794  POUSA0097278 {U2}.stl   
...            ...                    ...   
29346     10017082  POUSA0085214 {L2}.stl   
29347     10017210  POUSA0087329 {U2}.stl   
29348     10017210  POUSA0087329 {L2}.stl   
29349     10017205  POUSA0087258 {U2}.stl   
29350     10017205  POUSA0087258 {L2}.stl   

                                      relative_directory  \
0                avant/2021-12-02/SE/46020211126/SE57420   
1             avant/2022-04-11/NLD/31020220401/NLD183727   
2             avant/2022-04-11/NLD/31020220401/NLD183727   
3                avant/2022-03-16/SE/46020220309/DK59888   
4             avant/2021-12-01/USA/10017794/POUSA0097278   
...                                                  ...   
29346  herbst_advance/2021-08-21/USA/10017082/POUSA00...   
29347  herbst_advance/2021-08-21/USA/10017210/POUSA00...   
29348  herbst_advance/2021-08-21/USA/10017210/POUSA00...   
29349  herbst_advance/2021-08-21/USA/10017205/POUSA00...   
29350  herbst_advance/2021-08-21/USA/10017205/POUSA00...   

                                  arch_cad_fit  first_cam_retention_left  ...  \
0           features/SE57420_lower_cad_fit.stl                   26.8255  ...   
1         features/NLD183727_upper_cad_fit.stl                   30.9144  ...   
2         features/NLD183727_lower_cad_fit.stl                   28.5548  ...   
3           features/DK59888_upper_cad_fit.stl                   36.5898  ...   
4      features/POUSA0097278_upper_cad_fit.stl                   36.6598  ...   
...                                        ...                       ...  ...   
29346  features/POUSA0085214_lower_cad_fit.stl                   21.8962  ...   
29347  features/POUSA0087329_upper_cad_fit.stl                   28.3471  ...   
29348  features/POUSA0087329_lower_cad_fit.stl                   33.5498  ...   
29349  features/POUSA0087258_upper_cad_fit.stl                   47.8918  ...   
29350  features/POUSA0087258_lower_cad_fit.stl                   46.4529  ...   

       left_x_mm  left_y_mm  left_z_mm  anterior_x_mm  anterior_y_mm  \
0      24.604260 -18.499378  -5.474170       3.375185     -40.418022   
1      25.574125 -13.229218  12.019307       2.804521     -42.477430   
2      29.925974  -4.831328  -7.958755       2.173682     -45.724625   
3      17.416180   2.663425   7.327848      -1.554393     -18.880745   
4      22.911032   6.383784  18.966135       2.083402     -19.406360   
...          ...        ...        ...            ...            ...   
29346  26.688180   8.746353  -3.035197       2.749970     -22.266230   
29347  28.325115  11.770438   6.698221       3.092715     -14.743164   
29348  24.300356   5.263651 -11.274621       1.664177     -16.935926   
29349  24.252838 -31.197180  12.481576       3.159237     -52.430264   
29350  21.650667 -32.588074  -3.9584

In [25]:
cols = list(raw_df.columns)
# cols.remove('arch_scan')
df = raw_df.dropna(subset=cols)
print(f"dropped {len(raw_df)-len(df)} arches")
df.reset_index(inplace=True, drop=True)
df

dropped 24 arches


case_id   side first_cam_retention_date         product country  \
0           SE57420  lower               2021-12-02           avant      SE   
1         NLD183727  upper               2022-04-11           avant     NLD   
2         NLD183727  lower               2022-04-11           avant     NLD   
3           DK59888  upper               2022-03-16           avant      SE   
4      POUSA0097278  upper               2021-12-01           avant     USA   
...             ...    ...                      ...             ...     ...   
29322  POUSA0085214  lower               2021-08-21  herbst_advance     USA   
29323  POUSA0087329  upper               2021-08-21  herbst_advance     USA   
29324  POUSA0087329  lower               2021-08-21  herbst_advance     USA   
29325  POUSA0087258  upper               2021-08-21  herbst_advance     USA   
29326  POUSA0087258  lower               2021-08-21  herbst_advance     USA   

             batch       arch_cad_stage_2  \
0      46020211126       SE57420 {L2}.stl   
1      31020220401     NLD183727 {U2}.stl   
2      31020220401     NLD183727 {L2}.stl   
3      46020220309       DK59888 {U2}.stl   
4         10017794  POUSA0097278 {U2}.stl   
...            ...                    ...   
29322     10017082  POUSA0085214 {L2}.stl   
29323     10017210  POUSA0087329 {U2}.stl   
29324     10017210  POUSA0087329 {L2}.stl   
29325     10017205  POUSA0087258 {U2}.stl   
29326     10017205  POUSA0087258 {L2}.stl   

                                      relative_directory  \
0                avant/2021-12-02/SE/46020211126/SE57420   
1             avant/2022-04-11/NLD/31020220401/NLD183727   
2             avant/2022-04-11/NLD/31020220401/NLD183727   
3                avant/2022-03-16/SE/46020220309/DK59888   
4             avant/2021-12-01/USA/10017794/POUSA0097278   
...                                                  ...   
29322  herbst_advance/2021-08-21/USA/10017082/POUSA00...   
29323  herbst_advance/2021-08-21/USA/10017210/POUSA00...   
29324  herbst_advance/2021-08-21/USA/10017210/POUSA00...   
29325  herbst_advance/2021-08-21/USA/10017205/POUSA00...   
29326  herbst_advance/2021-08-21/USA/10017205/POUSA00...   

                                  arch_cad_fit  first_cam_retention_left  ...  \
0           features/SE57420_lower_cad_fit.stl                   26.8255  ...   
1         features/NLD183727_upper_cad_fit.stl                   30.9144  ...   
2         features/NLD183727_lower_cad_fit.stl                   28.5548  ...   
3           features/DK59888_upper_cad_fit.stl                   36.5898  ...   
4      features/POUSA0097278_upper_cad_fit.stl                   36.6598  ...   
...                                        ...                       ...  ...   
29322  features/POUSA0085214_lower_cad_fit.stl                   21.8962  ...   
29323  features/POUSA0087329_upper_cad_fit.stl                   28.3471  ...   
29324  features/POUSA0087329_lower_cad_fit.stl                   33.5498  ...   
29325  features/POUSA0087258_upper_cad_fit.stl                   47.8918  ...   
29326  features/POUSA0087258_lower_cad_fit.stl                   46.4529  ...   

       left_x_mm  left_y_mm  left_z_mm  anterior_x_mm  anterior_y_mm  \
0      24.604260 -18.499378  -5.474170       3.375185     -40.418022   
1      25.574125 -13.229218  12.019307       2.804521     -42.477430   
2      29.925974  -4.831328  -7.958755       2.173682     -45.724625   
3      17.416180   2.663425   7.327848      -1.554393     -18.880745   
4      22.911032   6.383784  18.966135       2.083402     -19.406360   
...          ...        ...        ...            ...            ...   
29322  26.688180   8.746353  -3.035197       2.749970     -22.266230   
29323  28.325115  11.770438   6.698221       3.092715     -14.743164   
29324  24.300356   5.263651 -11.274621       1.664177     -16.935926   
29325  24.252838 -31.197180  12.481576       3.159237     -52.430264   
29326  21.650667 -32.588074  -3.9584

In [26]:
root_dir = Path('/ssd/dataset_som_retention')
# df = pd.read_csv(root_dir.joinpath('retention_dataset_2022_01_21.csv'))
# df
case = df.iloc[0]
case

case_id                                                         SE57420
side                                                              lower
first_cam_retention_date                                     2021-12-02
product                                                           avant
country                                                              SE
batch                                                       46020211126
arch_cad_stage_2                                       SE57420 {L2}.stl
relative_directory              avant/2021-12-02/SE/46020211126/SE57420
arch_cad_fit                         features/SE57420_lower_cad_fit.stl
first_cam_retention_left                                        26.8255
first_cam_retention_anterior                                    37.7826
first_cam_retention_right                                       35.5842
hole_search_failed                                                False
left_x_mm                                                      2

In [27]:
df[df.first_cam_retention_anterior>100].describe()

first_cam_retention_left  first_cam_retention_anterior  \
count               8748.000000                   8748.000000   
mean                  43.020872                    130.160594   
std                   17.355168                     27.874008   
min                    5.033330                    100.013000   
25%                   31.159750                    109.865250   
50%                   41.061350                    121.841000   
75%                   52.512075                    142.848250   
max                  193.306000                    328.810000   

       first_cam_retention_right    left_x_mm    left_y_mm    left_z_mm  \
count                8748.000000  8748.000000  8748.000000  8748.000000   
mean                   43.849837    23.249227     0.116002     1.151491   
std                    18.114975     4.099688    13.897656    11.456371   
min                     2.583780   -10.032557   -35.891457   -43.710650   
25%                    31.405675    20.957594   -12.971740    -9.065182   
50%                    41.600450    23.106517     4.490581     2.649521   
75%                    54.312450    25.474851     9.038186     8.778161   
max                   180.011000    64.523790   142.272600    67.732700   

       anterior_x_mm  anterior_y_mm  anterior_z_mm   right_x_mm   right_y_mm  \
count    8748.000000    8748.000000    8748.000000  8748.000000  8748.000000   
mean        0.941256     -24.231190       1.705941   -21.212090     0.110866   
std         3.728463      13.507013      12.623306     4.121445    13.876260   
min       -34.300330     -61.330450     -44.050137   -58.581930   -38.404907   
25%        -0.865907     -38.831119     -10.025670   -23.419070   -12.997501   
50%         0.583952     -19.293697       4.302669   -21.329538     4.413092   
75%         2.683941     -15.844871      10.373075   -18.967267     9.065344   
max        39.846680     109.472770      69.397200    16.762293   138.974290   

        right_z_mm  
count  8748.000000  
mean      1.106465  
std      11.476733  
min     -43.412250  
25%      -9.061984  
50%       2.570308  
75%       8.766573  
max      67.790245

In [28]:
path = root_dir.joinpath(case.relative_directory, case.arch_cad_stage_2)
print(path)
mesh = som.load_STL(root_dir.joinpath(case.relative_directory, case.arch_cad_stage_2))
print(mesh)

/ssd/dataset_som_retention/avant/2021-12-02/SE/46020211126/SE57420/SE57420 {L2}.stl
SomnoMed.Trimesh (V1.8.2) 0x7fc78a654f10: Faces = 217,864, Vertices = 108,934, Memory = 8.31 MiB


In [29]:
print(mesh.edges_nonunique.shape)
print(mesh.edges_unique.shape)
print(mesh.edges_unique_map.shape)
print(np.unique(mesh.edges_unique_map).shape)
print(mesh.edges_unique)
print(np.concatenate((mesh.edges_unique, mesh.edges_unique[:,::-1]), axis=0))


(653592, 2)
(326796, 2)
(653592,)
(326796,)
[[     0  28553]
 [     0  37261]
 [     0  38588]
 ...
 [108419 108534]
 [108524 108791]
 [108581 108727]]
[[     0  28553]
 [     0  37261]
 [     0  38588]
 ...
 [108534 108419]
 [108791 108524]
 [108727 108581]]


In [30]:
print("\n# Vertices: {}, {}".format(mesh.vertices, mesh.vertices.shape))
print("\n# Vertex normals: {}, {}".format(mesh.vertices_normal, mesh.vertices_normal.shape))
print("\n# Faces: {}, {}".format(mesh.faces, mesh.faces.shape))
print("\n# Edges: {}, {}".format(mesh.edges_unique, mesh.edges_unique.shape))
print("\n# Edges Length: {}, {}".format(mesh.edges_unique_length, mesh.edges_unique_length.shape))


# Vertices: [[-38.01087952  -7.91697788   1.09488499]
 [  9.17760277 -23.50011253   3.89651036]
 [-28.17536163  -0.5620786   -4.2599225 ]
 ...
 [-15.08097363  24.12022209  -0.45625895]
 [-37.36065292  -3.43083119  -0.24120662]
 [-28.83584976  17.2467823    6.01201868]], (108934, 3)

# Vertex normals: [[-0.90546626 -0.42396291  0.01965481]
 [ 0.44560387  0.77653647 -0.44545293]
 [ 0.46824263  0.24693511 -0.84839371]
 ...
 [ 0.86291468 -0.50446504 -0.02988773]
 [ 0.93867918 -0.156043   -0.30746052]
 [-0.41560969  0.35784334  0.83619181]], (108934, 3)

# Faces: [[  7746  23487   2445]
 [ 30871  39498  51055]
 [ 21845  29627  61929]
 ...
 [ 80691 104929 105603]
 [106949   9318  57613]
 [106949  57613  26544]], (217864, 3)

# Edges: [[     0  28553]
 [     0  37261]
 [     0  38588]
 ...
 [108419 108534]
 [108524 108791]
 [108581 108727]], (326796, 2)

# Edges Length: [0.27925058 0.30372074 0.33513868 ... 0.1969642  0.25267993 0.35187835], (326796,)


In [31]:
def assert_rd_frame(mesh, side, debug=False):
    mins = mesh.vertices.min(axis=0)
    maxs = mesh.vertices.max(axis=0)
    ranges = maxs - mins
    if debug:
        print(mins, maxs, ranges)
    
    ## Test if z-axis is correct
    # test z-range is smaller than x/y-range
    assert ranges[2] == ranges.min(), "z-axis in not aligned to OTP"
    # z-axis alignment
    assert ranges[2] <= 20, "z-axis thickness exceeds blank thickness"
    # z-axis polarity
    if side.lower() == 'lower':
        assert mesh.vertices_normal[:,2].mean() < 0, "z-axis is in the wrong direction"
    else:
        assert mesh.vertices_normal[:,2].mean() > 0, "z-axis is in the wrong direction"

    # Test if y-axis is posterior
    max_y = maxs[1]
    min_y = mins[1]
    x_at_max_y = mesh.vertices[np.where(mesh.vertices[:,1]==max_y)][0,0] 
    x_at_min_y = mesh.vertices[np.where(mesh.vertices[:,1]==min_y)][0,0] 

    assert abs(x_at_min_y) < 15, "Most anterior x-coord should be within +/-15mm of y-axis"
    assert abs(x_at_max_y) > 15, "Most posterior x-coord should be greater than +/-15mm from y-axis"

In [32]:
def gen_retention_hole_features(mesh, hole_coord):
    """ Generates the displacment from every vertex to a single retention hole
    
    inputs:
        mesh:
            fit surface mesh in rd frame, som.Trimesh
        hole_coord:
            Array of np.array([x, y, z]).
    outputs:
        v_to_hole_distances:
            distance (mm) from vertex to retention hole
        v_to_hole_normals:
            normals from vertex to retention holes
        
    """
    assert isinstance(hole_coord, np.ndarray)
    assert hole_coord.shape == (3,)

    # Only calculate x-y plane normals and lengths
    v_to_hole_vectors = hole_coord[:2]-mesh.vertices[:, :2]
    v_to_hole_distances = np.linalg.norm(v_to_hole_vectors, axis=1)
    v_to_hole_vectors_normals = v_to_hole_vectors/ v_to_hole_distances[:, np.newaxis]
    return v_to_hole_vectors_normals, v_to_hole_distances

In [33]:
case

case_id                                                         SE57420
side                                                              lower
first_cam_retention_date                                     2021-12-02
product                                                           avant
country                                                              SE
batch                                                       46020211126
arch_cad_stage_2                                       SE57420 {L2}.stl
relative_directory              avant/2021-12-02/SE/46020211126/SE57420
arch_cad_fit                         features/SE57420_lower_cad_fit.stl
first_cam_retention_left                                        26.8255
first_cam_retention_anterior                                    37.7826
first_cam_retention_right                                       35.5842
hole_search_failed                                                False
left_x_mm                                                      2

In [39]:
%%time
import pymeshlab
import trimesh
from multiprocessing import Pool
desired_train_dataset_size=800
desired_test_dataset_size=50
decimation=950


# make dataset dir structure
dataset_name = 'ul_1k_fit'
paths = [
    f'datasets/{dataset_name}/upper/train/',
    f'datasets/{dataset_name}/upper/test/',
    f'datasets/{dataset_name}/lower/train/',
    f'datasets/{dataset_name}/lower/test/',
]
for path in paths:
    os.makedirs(path, exist_ok=True)



def process_row(root_dir, row, train_test):
    case_dir = root_dir.joinpath(row.relative_directory)
    path = f'datasets/{dataset_name}/{row.side.lower()}/{train_test}/{row.case_id}_{row.side.lower()}.obj'
    try:
        mesh = trimesh.load(case_dir.joinpath(row.arch_cad_fit))
        # assert_rd_frame(mesh, row.side.lower(), debug=False)
        if mesh is None:# or scan_mesh is None:
            return
    except Exception as err:
        print(err)
        return
        
    # DECIMATION
    if decimation != 0:
        mesh = mesh.simplify_quadratic_decimation(decimation)
        

    # if row.side.lower() == 'upper':
    #     # Flip uppers to face upwards like a lower
    #     transform = som.Transform(rotation=(0,180,0), degrees=True)
    #     mesh.apply_transform(transform)

    # Stage 1 cleaning
    trimesh.repair.fix_inversion(mesh)
    trimesh.repair.fill_holes(mesh)
    trimesh.repair.fix_normals(mesh)
    mesh.export(path)

    # Stage 2 cleaning
    ms = pymeshlab.MeshSet()
    ms.load_new_mesh(str(path))
    ms.meshing_remove_null_faces()
    ms.meshing_remove_duplicate_faces()
    ms.meshing_remove_duplicate_vertices()
    ms.meshing_repair_non_manifold_edges(method='Remove Faces')
    ms.meshing_repair_non_manifold_vertices()
    ms.meshing_remove_connected_component_by_face_number(mincomponentsize=int(decimation*0.9), removeunref=True)
    ms.meshing_remove_unreferenced_vertices()
    ms.save_current_mesh(str(path))
    ms.clear()
    
    
    # Print results
    mesh = som.load(path)
    final_result = str("{} {} {} {} {} {} {}: {}".format(mesh.is_connected, mesh.is_closed,  mesh.is_watertight, mesh.is_self_intersecting, mesh.is_smooth, mesh.is_manifold, len(mesh.split()), path))
    print(final_result)
    
    # if len(mesh.edges_unique) != int(decimation*1.5) or not mesh.is_manifold or not mesh.is_closed:
    #     os.remove(path)
        

args = []
count = 0
for _, row in df.iterrows():
    if count < desired_train_dataset_size:
        args.append((root_dir, row, 'train'))
    elif count < desired_train_dataset_size+desired_test_dataset_size:
        args.append((root_dir, row, 'test'))
    else:
        break
    count +=1

print(len(args))
# for arg in args:
#     print(arg[0], arg[2])
#     assert(len(arg)==3)
#     assert(type(arg[0]) != bool)
#     assert(type(arg[1]) != bool)
#     assert(type(arg[2]) != bool)

with Pool(processes=48) as pool:
    pool.starmap(process_row, args)

    


850


Data not utf-8! Trying None (confidence 0.0)
Data not utf-8! Trying TIS-620 (confidence 0.22725550233862957)
Data not utf-8! Trying Windows-1253 (confidence 0.5723146234780246)
Data not utf-8! Trying Windows-1253 (confidence 0.34974782545879285)
Data not utf-8! Trying None (confidence 0.0)
Data not utf-8! Trying TIS-620 (confidence 0.22079938011310032)
Data not utf-8! Trying TIS-620 (confidence 0.3298361110331498)
Data not utf-8! Trying IBM866 (confidence 0.5546448003500576)
Data not utf-8! Trying None (confidence 0.0)
Data not utf-8! Trying None (confidence 0.0)
Data not utf-8! Trying Windows-1253 (confidence 0.24224957607535433)
Data not utf-8! Trying Windows-1254 (confidence 0.22021788710098386)
Data not utf-8! Trying None (confidence 0.0)
Data not utf-8! Trying TIS-620 (confidence 0.21989074068876654)
Data not utf-8! Trying None (confidence 0.0)
Data not utf-8! Trying None (confidence 0.0)
Data not utf-8! Trying windows-1251 (confidence 0.3800537374267365)
Data not utf-8! Trying wi

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake ser

WARNING - 2022-05-30 16:23:05,061 - util - Data not utf-8! Trying windows-1251 (confidence 0.22425531090397496)


Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.

[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.

Jupyter environment detected. Enabling Open3D WebVisualizer.Jupyter environment detected. Enabling Open3D WebVisualizer.[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.
[Open3D INFO] WebRTC GUI backend enabled.
Jupyter environment detected. Enabling Open3D WebVisualizer.Jupyter environment detected. Enabling Open3D WebVisualizer.
Jupyter environment detected. Enabling Open3D WebVisualizer.

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.[Open3D INFO] WebRTC GUI backend enabled.


[Open3D INFO] WebRTC GUI backend enabled.[Open3D INFO] WebRTC GUI backend enabled.[Open3D INFO] WebRTCWin

...

True False False True False True 1: datasets/ul_1k_fit/lower/train/POUSA0107393_lower.obj
True False False True False True 1: datasets/ul_1k_fit/upper/train/SE59739_upper.obj
True False False True False True 1: datasets/ul_1k_fit/lower/train/SE59737_lower.obj
True False False True False True 1: datasets/ul_1k_fit/upper/test/POUSA0097243_upper.obj


WARNING - 2022-05-30 16:24:04,262 - util - Data not utf-8! Trying TIS-620 (confidence 0.23466600784967184)


True False False True False True 1: datasets/ul_1k_fit/upper/train/POAUS0032677_upper.obj
True False False True False True 1: datasets/ul_1k_fit/upper/train/POAUS0032742_upper.obj
True False False True False True 1: datasets/ul_1k_fit/upper/test/POUSA0107291_upper.obj


WARNING - 2022-05-30 16:24:04,623 - util - Data not utf-8! Trying None (confidence 0.0)


True False False True False True 1: datasets/ul_1k_fit/upper/test/SE59757_upper.obj
True False False True False True 1: datasets/ul_1k_fit/upper/test/SE59746_upper.obj
True False False True False True 1: datasets/ul_1k_fit/upper/test/NLD180317_upper.obj
True False False True False True 1: datasets/ul_1k_fit/upper/test/SE59776_upper.obj
True False False True False True 1: datasets/ul_1k_fit/lower/test/SE59727_lower.obj
True False False True False True 1: datasets/ul_1k_fit/lower/test/NO69293_lower.obj
True False False True False True 1: datasets/ul_1k_fit/lower/test/nl180032_lower.obj
True False False True False True 1: datasets/ul_1k_fit/upper/test/POUSA0107599_upper.obj
True False False True False True 1: datasets/ul_1k_fit/lower/test/POUSA0107291_lower.obj
True False False True False True 1: datasets/ul_1k_fit/upper/test/nl180076_upper.obj
CPU times: user 1.31 s, sys: 1.46 s, total: 2.77 s
Wall time: 1min 7s


In [40]:
shrec_dir =  Path('datasets/shrec_16')

for path in shrec_dir.glob("*/*/*.obj"):
    mesh = som.load(path)
    final_result = str("{} {} {} {} {} {} {}: {} : {}".format(mesh.is_connected, mesh.is_closed,  mesh.is_watertight, mesh.is_self_intersecting, mesh.is_smooth, mesh.is_manifold, len(mesh.split()), path, mesh))
    print(final_result)
    


True True False True False True 1: datasets/shrec_16/bird2/train/T83.obj : SomnoMed.Trimesh (V1.8.2) 0x7fc8d8ed7310: Faces = 500, Vertices = 252, Memory = 0.04 MiB
True True False True False True 1: datasets/shrec_16/bird2/train/T130.obj : SomnoMed.Trimesh (V1.8.2) 0x7fc8d8ed74c0: Faces = 500, Vertices = 252, Memory = 0.04 MiB
True True False True False True 1: datasets/shrec_16/bird2/train/T584.obj : SomnoMed.Trimesh (V1.8.2) 0x7fc8d8ed75e0: Faces = 500, Vertices = 252, Memory = 0.04 MiB
True True False True False True 1: datasets/shrec_16/bird2/train/T417.obj : SomnoMed.Trimesh (V1.8.2) 0x7fc8d8ed7490: Faces = 500, Vertices = 252, Memory = 0.04 MiB
True True False True False True 1: datasets/shrec_16/bird2/train/T520.obj : SomnoMed.Trimesh (V1.8.2) 0x7fc8d8ed7040: Faces = 500, Vertices = 252, Memory = 0.04 MiB
True True False True False True 1: datasets/shrec_16/bird2/train/T500.obj : SomnoMed.Trimesh (V1.8.2) 0x7fc8d8ed72b0: Faces = 500, Vertices = 252, Memory = 0.04 MiB
True True F

In [41]:

shrec_dir =  Path('datasets/ul_1k_fit')

for path in shrec_dir.glob("*/*/*.obj"):
    mesh = som.load(path)
    final_result = str("{} {} {} {} {} {} {}: {} {}: {}".format(mesh.is_connected, mesh.is_closed,  mesh.is_watertight, mesh.is_self_intersecting, mesh.is_smooth, mesh.is_manifold, len(mesh.split()), len(mesh.edges_unique), path, mesh))
    print(final_result)

True False False True False True 1: 1464 datasets/ul_1k_fit/lower/train/POUSA0107251_lower.obj: SomnoMed.Trimesh (V1.8.2) 0x7fc8d8ed7400: Faces = 950, Vertices = 515, Memory = 0.09 MiB
True False False True False True 1: 1466 datasets/ul_1k_fit/lower/train/SE59927_lower.obj: SomnoMed.Trimesh (V1.8.2) 0x7fc8d8ed7640: Faces = 949, Vertices = 518, Memory = 0.09 MiB
True False False True False True 1: 1468 datasets/ul_1k_fit/lower/train/SE59929_lower.obj: SomnoMed.Trimesh (V1.8.2) 0x7fc8d8ed7580: Faces = 949, Vertices = 520, Memory = 0.09 MiB
True False False True False True 1: 1464 datasets/ul_1k_fit/lower/train/POUSA0107381_lower.obj: SomnoMed.Trimesh (V1.8.2) 0x7fc8d8ed7400: Faces = 950, Vertices = 515, Memory = 0.09 MiB
True False False True False True 1: 1463 datasets/ul_1k_fit/lower/train/nl180802_lower.obj: SomnoMed.Trimesh (V1.8.2) 0x7fc8d8ed7580: Faces = 949, Vertices = 515, Memory = 0.09 MiB
True False False True False True 1: 1463 datasets/ul_1k_fit/lower/train/POUSA0107513_lowe

In [114]:
case_dir = root_dir.joinpath(case.relative_directory)
mesh_path = case_dir.joinpath(case.arch_cad_stage_2)

mesh = trimesh.load(mesh_path)
mesh.show()

/home/josh/.local/lib/python3.8/site-packages/IPython/core/display.py:419: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


In [106]:
print(mesh)
dec_mesh = mesh.simplify_quadratic_decimation(2000)
print(len(dec_mesh.edges_unique))
dec_mesh.show()

<trimesh.Trimesh(vertices.shape=(108934, 3), faces.shape=(217864, 3))>
3000


/home/josh/.local/lib/python3.8/site-packages/IPython/core/display.py:419: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")
